In [1]:
import stellargraph as sg
from stellargraph.data import EdgeSplitter
from stellargraph.mapper import GraphSAGELinkGenerator
from stellargraph.layer import GraphSAGE, HinSAGE, link_classification
import networkx as nx
from tensorflow import keras
from sklearn import preprocessing, feature_extraction, model_selection
from stellargraph import StellarGraph
from stellargraph import globalvar
from stellargraph import datasets
from IPython.display import display, HTML
from stellargraph.mapper import FullBatchLinkGenerator
import matplotlib.pyplot as plt
from math import isclose
from sklearn.decomposition import PCA
import os
import networkx as nx
import numpy as np
import pandas as pd
from stellargraph import StellarGraph, datasets
from stellargraph.data import EdgeSplitter
from collections import Counter
import multiprocessing
from IPython.display import display, HTML
from sklearn.model_selection import train_test_split
import networkx as nx
from stellargraph.mapper import GraphWaveGenerator
from stellargraph import StellarGraph
from sklearn.decomposition import PCA
import numpy as np
from matplotlib import pyplot as plt
from scipy.sparse.linalg import eigs
import tensorflow as tf
from tensorflow.keras import backend as K
%matplotlib inline

In [2]:
nx_data = nx.read_graphml("2012-12-02.graphml")

In [3]:
df_edges = nx.to_pandas_edgelist(nx_data)

In [4]:
df_edges

source    target  n_tx         value
0      81567039  81567155     1  1.139179e+12
1      81567039  81567156     1  1.019400e+08
2      81567155  81568176     1  1.114108e+12
3      81567155       221     1  2.507104e+10
4      81526809  79800777     1  6.059134e+08
...         ...       ...   ...           ...
24862  81573965  79526935     1  4.000000e+06
24863  81573966  81573967     1  3.386418e+07
24864  81573966  79526935     1  4.000000e+06
24865  81573967  81573968     1  3.281418e+07
24866  81573967  79526935     1  1.000000e+06

[24867 rows x 4 columns]

In [44]:
g = StellarGraph.from_networkx(nx_data,edge_weight_attr="value")

In [6]:
print(g.info())

StellarDiGraph: Directed multigraph
 Nodes: 13093, Edges: 24867

 Node types:
  default: [13093]
    Features: none
    Edge types: default-default->default

 Edge types:
    default-default->default: [24867]
        Weights: range=[1, 1.13918e+12], mean=3.78465e+09, std=5.54065e+10
        Features: none


In [7]:
edge_splitter_test = EdgeSplitter(g)

In [8]:


# Randomly sample a fraction p=0.1 of all positive links, and same number of negative links, from graph, and obtain the
# reduced graph graph_test with the sampled links removed:
graph_test, examples_test, labels_test = edge_splitter_test.train_test_split(
    p=0.1, method="global"
)

print(graph_test.info())

** Sampled 2486 positive and 2486 negative edges. **
StellarDiGraph: Directed multigraph
 Nodes: 13093, Edges: 22381

 Node types:
  default: [13093]
    Features: none
    Edge types: default-default->default

 Edge types:
    default-default->default: [22381]
        Weights: range=[1, 1.13918e+12], mean=3.81413e+09, std=5.5821e+10
        Features: none


In [9]:
# Do the same process to compute a training subset from within the test graph
edge_splitter_train = EdgeSplitter(graph_test, g)
graph_train, examples, labels = edge_splitter_train.train_test_split(
    p=0.1, method="global"
)
(
    examples_train,
    examples_model_selection,
    labels_train,
    labels_model_selection,
) = train_test_split(examples, labels, train_size=0.75, test_size=0.25)

print(graph_train.info())

** Sampled 2238 positive and 2238 negative edges. **
StellarDiGraph: Directed multigraph
 Nodes: 13093, Edges: 20143

 Node types:
  default: [13093]
    Features: none
    Edge types: default-default->default

 Edge types:
    default-default->default: [20143]
        Weights: range=[1, 1.13918e+12], mean=3.95648e+09, std=5.69712e+10
        Features: none


In [11]:
print(graph_train.info())

StellarDiGraph: Directed multigraph
 Nodes: 13093, Edges: 20143

 Node types:
  default: [13093]
    Features: none
    Edge types: default-default->default

 Edge types:
    default-default->default: [20143]
        Weights: range=[1, 1.13918e+12], mean=3.95648e+09, std=5.69712e+10
        Features: none


In [13]:
print(graph_test.info())

StellarDiGraph: Directed multigraph
 Nodes: 13093, Edges: 22381

 Node types:
  default: [13093]
    Features: none
    Edge types: default-default->default

 Edge types:
    default-default->default: [22381]
        Weights: range=[1, 1.13918e+12], mean=3.81413e+09, std=5.5821e+10
        Features: none


In [26]:
pd.DataFrame(
    [
        (
            "Training Set",
            len(examples_train),
            "Train Graph",
            "Test Graph",
            "Train the Link Classifier",
        ),
        (
            "Model Selection",
            len(examples_model_selection),
            "Train Graph",
            "Test Graph",
            "Select the best Link Classifier model",
        ),
        (
            "Test set",
            len(examples_test),
            "Test Graph",
            "Full Graph",
            "Evaluate the best Link Classifier",
        ),
    ],
    columns=("Split", "Number of Examples", "Hidden from", "Picked from", "Use"),
).set_index("Split")

Number of Examples  Hidden from Picked from  \
Split                                                          
Training Set                   3357  Train Graph  Test Graph   
Model Selection                1119  Train Graph  Test Graph   
Test set                       4972   Test Graph  Full Graph   

                                                   Use  
Split                                                   
Training Set                 Train the Link Classifier  
Model Selection  Select the best Link Classifier model  
Test set             Evaluate the best Link Classifier

In [54]:
def node2vec_embedding(G):
    sample_points = np.linspace(0, 100, 50).astype(np.float32)
    degree = 20
    scales = [5, 10]

    generator = GraphWaveGenerator(G, scales=scales, degree=degree)

    embeddings_dataset = generator.flow(
        node_ids=G.nodes(), sample_points=sample_points, batch_size=1, repeat=False
    )

    embeddings = [x.numpy() for x in embeddings_dataset]

    return embeddings

In [55]:
embedding_train = node2vec_embedding(graph_train)

In [56]:
embedding_train

[array([[1.00000000e+00, 1.00000000e+00, 1.00000000e+00, 1.00000000e+00,
         9.99999940e-01, 1.00000000e+00, 9.99999821e-01, 1.00000000e+00,
         9.99999762e-01, 1.00000000e+00, 9.99999702e-01, 1.00000000e+00,
         9.99999523e-01, 1.00000000e+00, 9.99999404e-01, 1.00000000e+00,
         9.99999166e-01, 1.00000000e+00, 9.99998927e-01, 1.00000000e+00,
         9.99998748e-01, 1.00000000e+00, 9.99998510e-01, 1.00000000e+00,
         9.99998212e-01, 1.00000000e+00, 9.99997914e-01, 1.00000000e+00,
         9.99997616e-01, 1.00000000e+00, 9.99997139e-01, 1.00000000e+00,
         9.99996841e-01, 1.00000000e+00, 9.99996424e-01, 1.00000000e+00,
         9.99995947e-01, 1.00000000e+00, 9.99995530e-01, 1.00000000e+00,
         9.99995053e-01, 1.00000000e+00, 9.99994576e-01, 1.00000000e+00,
         9.99994040e-01, 1.00000000e+00, 9.99993443e-01, 1.00000000e+00,
         9.99992907e-01, 1.00000000e+00, 9.99992311e-01, 1.00000000e+00,
         9.99991715e-01, 1.00000000e+00, 9.99991059

In [48]:
from sklearn.pipeline import Pipeline
from sklearn.linear_model import LogisticRegressionCV
from sklearn.metrics import roc_auc_score
from sklearn.preprocessing import StandardScaler


# 1. link embeddings
def link_examples_to_features(link_examples, transform_node, binary_operator):
    return [
        binary_operator(transform_node(src), transform_node(dst))
        for src, dst in link_examples
    ]


# 2. training classifier
def train_link_prediction_model(
    link_examples, link_labels, get_embedding, binary_operator
):
    clf = link_prediction_classifier()
    link_features = link_examples_to_features(
        link_examples, get_embedding, binary_operator
    )
    clf.fit(link_features, link_labels)
    return clf


def link_prediction_classifier(max_iter=2000):
    lr_clf = LogisticRegressionCV(Cs=10, cv=10, scoring="roc_auc", max_iter=max_iter)
    return Pipeline(steps=[("sc", StandardScaler()), ("clf", lr_clf)])


# 3. and 4. evaluate classifier
def evaluate_link_prediction_model(
    clf, link_examples_test, link_labels_test, get_embedding, binary_operator
):
    link_features_test = link_examples_to_features(
        link_examples_test, get_embedding, binary_operator
    )
    score = evaluate_roc_auc(clf, link_features_test, link_labels_test)
    return score


def evaluate_roc_auc(clf, link_features, link_labels):
    predicted = clf.predict_proba(link_features)

    # check which class corresponds to positive links
    positive_column = list(clf.classes_).index(1)
    return roc_auc_score(link_labels, predicted[:, positive_column])

In [49]:
def operator_l1(u, v):
    return np.abs(u - v)


def operator_l2(u, v):
    return (u - v) ** 2


def run_link_prediction(binary_operator):
    clf = train_link_prediction_model(
        examples_train, labels_train, embedding_train, binary_operator
    )
    score = evaluate_link_prediction_model(
        clf,
        examples_model_selection,
        labels_model_selection,
        embedding_train,
        binary_operator,
    )

    return {
        "classifier": clf,
        "binary_operator": binary_operator,
        "score": score,
    }


binary_operators = [operator_l1, operator_l2]


In [50]:
results = [run_link_prediction(op) for op in binary_operators]
best_result = max(results, key=lambda result: result["score"])

print(f"Best result from '{best_result['binary_operator'].__name__}'")

pd.DataFrame(
    [(result["binary_operator"].__name__, result["score"]) for result in results],
    columns=("name", "ROC AUC score"),
).set_index("name")

TypeError: 'numpy.ndarray' object is not callable

In [57]:
dataset = datasets.Cora()
display(HTML(dataset.description))
G, _ = dataset.load(subject_as_feature=True)

In [60]:
G.feature()

AttributeError: 'StellarGraph' object has no attribute 'feature'